In [2]:
import sys
!{sys.executable} -m pip install pandas-profiling

In [3]:
import pandas as pd
import numpy as np
import datetime as dt

import random
#import names
#import pandas_profiling
import warnings
warnings.filterwarnings("ignore")

import seaborn as sns
import matplotlib.pyplot as plt

import sklearn.model_selection
from sklearn import model_selection
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split

from sklearn.linear_model import LinearRegression
from sklearn import metrics
from sklearn.metrics import r2_score
from sklearn.ensemble import RandomForestRegressor
import xgboost
import csv as csv
from xgboost import plot_importance

data = pd.read_csv("camp_data.csv", parse_dates=['date'], dayfirst=True)

print (data.shape)
data.head(5)

(75205, 12)


date  business_vertical  country   region          city_code  \
0 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
1 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
2 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
3 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
4 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   

   strategy_id  channel_name  goal_type  total_spend_cpm  impressions  clicks  \
0      3714868             1        1.0       149.565425         48.0     0.0   
1      3715603             1        1.0       291.516169        124.0     1.0   
2      3716560             1        2.0       509.019147        415.0     0.0   
3      3718685             2        2.0       134.542628        218.0     0.0   
4      3718702             2        1.0         3.761886          1.0     0.0   

   conversions  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0

In [4]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 75205 entries, 0 to 75204
Data columns (total 12 columns):
 #   Column             Non-Null Count  Dtype         
---  ------             --------------  -----         
 0   date               75205 non-null  datetime64[ns]
 1   business_vertical  75205 non-null  int64         
 2   country            75205 non-null  int64         
 3   region             75205 non-null  object        
 4   city_code          75205 non-null  object        
 5   strategy_id        75205 non-null  int64         
 6   channel_name       75205 non-null  int64         
 7   goal_type          43062 non-null  float64       
 8   total_spend_cpm    75205 non-null  float64       
 9   impressions        73703 non-null  float64       
 10  clicks             73683 non-null  float64       
 11  conversions        73654 non-null  float64       
dtypes: datetime64[ns](1), float64(5), int64(4), object(2)
memory usage: 6.9+ MB


In [5]:
data.describe()

business_vertical       country   strategy_id  channel_name  \
count       75205.000000  75205.000000  7.520500e+04  75205.000000   
mean            0.572595      1.272110  3.764120e+06      0.834798   
std             0.494705      1.330626  3.403133e+04      0.813834   
min             0.000000      0.000000  3.714868e+06      0.000000   
25%             0.000000      0.000000  3.727983e+06      0.000000   
50%             1.000000      2.000000  3.771828e+06      1.000000   
75%             1.000000      2.000000  3.784636e+06      2.000000   
max             1.000000      7.000000  3.828492e+06      2.000000   

          goal_type  total_spend_cpm    impressions        clicks  conversions  
count  43062.000000     75205.000000   73703.000000  73683.000000      73654.0  
mean       1.476940       424.826770     291.512313      0.371049          0.0  
std        0.499474      5275.184032    4179.601279      7.118569          0.0  
min        1.000000         0.242250       0.000000      0.000000          0.0  
25%        1.000000         2.815800       1.000000      0.000000          0.0  
50%        1.000000         8.621250       4.000000      0.000000          0.0  
75%        2.000000        32.941426      18.000000      0.000000          0.0  
max        2.000000    374622.032272  374343.000000    661.000000          0.0

In [8]:
len(data.strategy_id.unique())

75

In [9]:
data.isnull().sum()

date                     0
business_vertical        0
country                  0
region                   0
city_code                0
strategy_id              0
channel_name             0
goal_type            32143
total_spend_cpm          0
impressions           1502
clicks                1522
conversions           1551
dtype: int64

In [10]:
data.goal_type.value_counts()

1.0    22524
2.0    20538
Name: goal_type, dtype: int64

In [11]:
#fill goal with majority class
data.goal_type= data.goal_type.fillna(value=1.0)

In [12]:
data.clicks.value_counts()

0.0      71121
1.0       1097
2.0        404
3.0        167
4.0        120
         ...  
184.0        1
87.0         1
120.0        1
233.0        1
97.0         1
Name: clicks, Length: 125, dtype: int64

In [13]:
#fill goal with majority class
data.clicks= data.clicks.fillna(value=0.0)

In [14]:
data.impressions.mean()

291.512312931631

In [15]:
#fill impressions with mean value
data.impressions= data.impressions.fillna(value=data.impressions.mean())

In [16]:
data.conversions.value_counts()

0.0    73654
Name: conversions, dtype: int64

In [17]:
#fill conversions with majority class
data.conversions= data.conversions.fillna(value=0.0)

In [18]:
#convert type to int for numerical columns
data['goal_type']= data['goal_type'].astype(int)
data['impressions']= data['impressions'].astype(int)
data['clicks']= data['clicks'].astype(int)

In [19]:
data.head()

date  business_vertical  country   region          city_code  \
0 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
1 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
2 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
3 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
4 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   

   strategy_id  channel_name  goal_type  total_spend_cpm  impressions  clicks  \
0      3714868             1          1       149.565425           48       0   
1      3715603             1          1       291.516169          124       1   
2      3716560             1          2       509.019147          415       0   
3      3718685             2          2       134.542628          218       0   
4      3718702             2          1         3.761886            1       0   

   conversions  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          0.0

In [20]:
#creating a new column Click through rate (ctr)

data['ctr'] = data.clicks*100/data.impressions

In [21]:
#creating a new column cost per click (cpc)

data['cpc'] = data.total_spend_cpm/data.clicks

In [22]:
data.head(5)

date  business_vertical  country   region          city_code  \
0 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
1 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
2 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
3 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
4 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   

   strategy_id  channel_name  goal_type  total_spend_cpm  impressions  clicks  \
0      3714868             1          1       149.565425           48       0   
1      3715603             1          1       291.516169          124       1   
2      3716560             1          2       509.019147          415       0   
3      3718685             2          2       134.542628          218       0   
4      3718702             2          1         3.761886            1       0   

   conversions       ctr         cpc  
0          0.0  0.000000         inf  
1          0.0  0.806452  291.516169  
2          0.0  0.000000         inf  
3          0.0  0.000000         inf  
4          0.0  0.000000         inf

In [23]:
#check for distribution
data.ctr.value_counts()

0.000000      63967
0.343643         45
0.687285         18
33.333333         8
100.000000        8
              ...  
0.176184          1
0.605275          1
0.149661          1
0.185376          1
0.659577          1
Name: ctr, Length: 1975, dtype: int64

In [24]:
#check for distribution
data.cpc.value_counts()

inf            72643
6.669000           3
597.802310         2
82.752992          2
712.245709         2
               ...  
2.563240           1
147.943765         1
780.861702         1
1521.100370        1
237.632564         1
Name: cpc, Length: 2510, dtype: int64

In [25]:
#drop column cpc as all values are infinity
data.drop(['cpc'], axis = 1, inplace = True)

In [26]:
#create new columns for week number and day from the date column

data['week'] = data['date'].dt.week
data['day'] = data['date'].dt.day

In [27]:
data.head(3)

date  business_vertical  country   region          city_code  \
0 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
1 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   
2 2018-09-17                  1        2  Aceh Sm  idn-ac-banda aceh   

   strategy_id  channel_name  goal_type  total_spend_cpm  impressions  clicks  \
0      3714868             1          1       149.565425           48       0   
1      3715603             1          1       291.516169          124       1   
2      3716560             1          2       509.019147          415       0   

   conversions       ctr  week  day  
0          0.0  0.000000    38   17  
1          0.0  0.806452    38   17  
2          0.0  0.000000    38   17

In [28]:
data.city_code.value_counts()

idn-jt-semarang        205
idn-ji-surabaya        204
idn-jk-jakarta         204
idn-jb-bandung         202
idn-jb-bogor           201
                      ... 
aus-sa-kyancutta         1
aus-tas-lachlan          1
mys-07-sungai bakap      1
aus-tas-ellendale        1
aus-nsw-the pocket       1
Name: city_code, Length: 3894, dtype: int64

In [29]:
data.region.value_counts()

New South Wales       12682
Victoria               8368
Queensland             6550
Jawa Timur             4398
Jawa Tengah            4304
                      ...  
Surigao Del Sur           1
Masbate                   1
Agusan Del Sur            1
Misamis Occidental        1
somalia                   1
Name: region, Length: 127, dtype: int64

In [30]:
#import other csv's
data_business = pd.read_csv("business_vertical.csv")
data_country = pd.read_csv("country.csv")
data_channel = pd.read_csv("channel_name.csv")

In [31]:
#merge csv to main data frame to create a new df

all_data = pd.merge(pd.merge(pd.merge(data, data_business, how='left', left_on=['business_vertical'], right_on=['label']), 
         data_country, how='left', left_on=['country'], right_on=['label']),
         data_channel, how='left', left_on=['channel_name'], right_on=['label'])

In [32]:
#drop duplicate columns
all_data = all_data.drop(['business_vertical_x',  'country_x', 'channel_name_x','label_x', 'label_y', 'label'], axis = 1, inplace= False)

#rename columns
all_data.rename(columns={'business_vertical_y': 'business_vertical', 'country_y': 'country', 'channel_name_y': 'channel_name'}, inplace=True)

In [33]:
print(all_data.shape)
all_data.head(5)


(75205, 15)


date   region          city_code  strategy_id  goal_type  \
0 2018-09-17  Aceh Sm  idn-ac-banda aceh      3714868          1   
1 2018-09-17  Aceh Sm  idn-ac-banda aceh      3715603          1   
2 2018-09-17  Aceh Sm  idn-ac-banda aceh      3716560          2   
3 2018-09-17  Aceh Sm  idn-ac-banda aceh      3718685          2   
4 2018-09-17  Aceh Sm  idn-ac-banda aceh      3718702          1   

   total_spend_cpm  impressions  clicks  conversions       ctr  week  day  \
0       149.565425           48       0          0.0  0.000000    38   17   
1       291.516169          124       1          0.0  0.806452    38   17   
2       509.019147          415       0          0.0  0.000000    38   17   
3       134.542628          218       0          0.0  0.000000    38   17   
4         3.761886            1       0          0.0  0.000000    38   17   

  business_vertical    country channel_name  
0           Finance  Indonesia      Display  
1           Finance  Indonesia      Display  
2           Finance  Indonesia      Display  
3           Finance  Indonesia       Mobile  
4           Finance  Indonesia       Mobile

In [34]:
data.isnull().sum()

date                    0
business_vertical       0
country                 0
region                  0
city_code               0
strategy_id             0
channel_name            0
goal_type               0
total_spend_cpm         0
impressions             0
clicks                  0
conversions             0
ctr                  8676
week                    0
day                     0
dtype: int64

In [35]:
data.ctr.mean()

0.05492378582228661

In [36]:
#fill ctr with mean value
data.ctr= data.ctr.fillna(value=data.ctr.mean())

In [37]:
#all null values removed
data.isnull().sum()

date                 0
business_vertical    0
country              0
region               0
city_code            0
strategy_id          0
channel_name         0
goal_type            0
total_spend_cpm      0
impressions          0
clicks               0
conversions          0
ctr                  0
week                 0
day                  0
dtype: int64

In [38]:
#T1.Q3: Find sum based on channel_name
all_data[['impressions','clicks','conversions']].groupby(by=[all_data['channel_name']]).sum().groupby(level=[0]).sum()

impressions  clicks  conversions
channel_name                                  
Display           5753862    3023          0.0
Mobile            9454463   13226          0.0
Unknown           6714089   11091          0.0

In [39]:
#Task1.Q3: Find sum based on country
all_data[['impressions','clicks','conversions']].groupby(by=[all_data['country']]).sum().groupby(level=[0]).sum()

impressions  clicks  conversions
country                                           
Australia              686768     192          0.0
Hong Kong             1034672    1643          0.0
Indonesia            19166155   24447          0.0
Malaysia               377021     645          0.0
New Zealand            648473     203          0.0
Philippines              9275     210          0.0
Somalia                     0       0          0.0
reserved/private           50       0          0.0

In [40]:
#Task1.Q3: Find sum based on business_vertical
all_data[['impressions','clicks','conversions']].groupby(by=[all_data['business_vertical']]).sum().groupby(level=[0]).sum()

impressions  clicks  conversions
business_vertical                                  
Finance               15208325   16249          0.0
Unknown                6714089   11091          0.0

In [41]:
#Task1.Q4: find cummalative sum for strategy id 3718750
data_filter = all_data[all_data['strategy_id'] == 3718750]

In [42]:
x = data_filter[['impressions','clicks']].groupby(by=[all_data['channel_name'],all_data['date']]).sum().groupby(level=[0]).cumsum()
x

impressions  clicks
channel_name date                           
Display      2018-09-17       200020     206
             2018-09-18       320680     314
             2018-09-19       413328     376
             2018-09-20       505129     458
             2018-09-21       517126     458
             2018-09-22       625158     565
             2018-09-23       724857     670
             2018-09-24       827140     808
             2018-09-25       942216     920
             2018-09-26      1060700    1067
Unknown      2018-09-27         9954      10

In [43]:
import pandas_profiling

In [44]:
import sys
print(sys.executable)
!pip install visions

C:\Users\HIMANSHUU\anaconda3\python.exe


In [45]:
!pip install -U pandas-profiling[notebook]
!jupyter nbextension enable --py widgetsnbextension

Enabling notebook extension jupyter-js-widgets/extension...
      - Validating: ok


In [46]:
#EDA of data from a new package that performs operations and gives insights for the df

profile = pandas_profiling.ProfileReport(all_data)
display(profile)

In [101]:
import matplotlib.pyplot as plt

sp1 = all_data["total_spend_cpm"]
sp2 = all_data["impressions"]

plt.scatter(sp1, sp2)
plt.show()

In [103]:
all_data["impressions"]

0         48
1        124
2        415
3        218
4          1
        ... 
75200     51
75201      5
75202      1
75203     52
75204    333
Name: impressions, Length: 75205, dtype: int32

In [ ]:
#making a pair plot to see linearity in data

sns.set(style="ticks", color_codes=True)
g = sns.pairplot(all_data)

In [47]:
#country with clicks

import matplotlib.pyplot as plt

fig, ax = plt.subplots(figsize=(20,5))
sns.set_context("poster")
current_palette = sns.diverging_palette(255, 133, l=60, n=7, center="dark")

fig = sns.barplot(x='country',y='clicks', data=all_data, palette=current_palette)

fig.set_ylabel("no of clicks")
fig.set_xlabel("country")

Text(0.5, 0, 'country')

In [48]:
#country with impressions

fig, ax = plt.subplots(figsize=(20,5))
sns.set_context("poster")
current_palette = sns.diverging_palette(255, 133, l=60, n=7, center="dark")

fig = sns.barplot(x='country',y='impressions', data=all_data, palette=current_palette)

fig.set_ylabel("no of impressions")
fig.set_xlabel("country")

Text(0.5, 0, 'country')

In [49]:
#channel_name with clicks
import seaborn as sns

fig, ax = plt.subplots(figsize=(20,5))
sns.set_context("poster")
current_palette = sns.diverging_palette(255, 133, l=60, n=7, center="dark")

fig = sns.barplot(x='channel_name',y='clicks', data=all_data, palette=current_palette)

fig.set_ylabel("no of clicks")
fig.set_xlabel("channel_name")

Text(0.5, 0, 'channel_name')

In [50]:
#channel_name with impressions

fig, ax = plt.subplots(figsize=(20,5))
sns.set_context("poster")
current_palette = sns.diverging_palette(255, 133, l=60, n=7, center="dark")

fig = sns.barplot(x='channel_name',y='impressions', data=all_data, palette=current_palette)

fig.set_ylabel("no of impressions")
fig.set_xlabel("channel_name")

Text(0.5, 0, 'channel_name')

In [51]:
#business_vertical with clicks

fig, ax = plt.subplots(figsize=(20,5))
sns.set_context("poster")
current_palette = sns.diverging_palette(255, 133, l=60, n=7, center="dark")

fig = sns.barplot(x='business_vertical',y='clicks', data=all_data, palette=current_palette)

fig.set_ylabel("no of clicks")
fig.set_xlabel("business_vertical")

Text(0.5, 0, 'business_vertical')

In [52]:
#business_vertical with impressions

fig, ax = plt.subplots(figsize=(20,5))
sns.set_context("poster")
current_palette = sns.diverging_palette(255, 133, l=60, n=7, center="dark")

fig = sns.barplot(x='business_vertical',y='impressions', data=all_data, palette=current_palette)

fig.set_ylabel("no of impressions")
fig.set_xlabel("business_vertical")

Text(0.5, 0, 'business_vertical')

In [53]:
#separate test and train

#1 Independent variables We remove date, strategy_id, region,city_code from independent variables as they being having high corelation
X=data[['business_vertical', 'country', 'channel_name', 'goal_type', 'total_spend_cpm', 'ctr', 'week', 'day']]

#2 Dependent variables
y1= data['impressions']
y2= data['clicks']

# IMPRESSIONS

In [54]:
#prediction of impressions
split_size=0.3

#Creation of Train and Test dataset
X_train, X_test, y_train, y_test = sklearn.model_selection.train_test_split(X,y1,test_size=split_size,random_state=22)

#Creation of Train and validation dataset
X_train, X_val, y_train, y_val = train_test_split(X_train,y_train,test_size=0.2,random_state=5)

In [55]:
print(X_train.shape)
print(y_test.shape)

(42114, 8)
(22562,)


# Linear Regression for impressions

In [56]:
#Build base linear model as the task is to make predictions with continuos dependent variables.
#fitting Linear Regression to the Training set

#Modelling of IMPRESSIONS

regressor = LinearRegression()
regressor.fit(X_train, y_train)

y_pred_linear = regressor.predict(X_test)

In [57]:
# Evaluating the Algorithm for test data

print('Mean Absolute Error:', metrics.mean_absolute_error(y_test, y_pred_linear))  
print('Mean Squared Error:', metrics.mean_squared_error(y_test, y_pred_linear))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_test, y_pred_linear)))
print('R square value is:',r2_score(y_test, y_pred_linear))

Mean Absolute Error: 191.80122325989382
Mean Squared Error: 4294142.552244263
Root Mean Squared Error: 2072.2312979598255
R square value is: 0.7993697459673825


In [58]:
#VALIDATION accuracy for LR for IMPRESSIONS

y_pred_linear_val = regressor.predict(X_val)
print('Mean Absolute Error:', metrics.mean_absolute_error(y_val, y_pred_linear_val))  
print('Mean Squared Error:', metrics.mean_squared_error(y_val, y_pred_linear_val))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_val, y_pred_linear_val)))
print('R square value is:',r2_score(y_val, y_pred_linear_val))

Mean Absolute Error: 135.61982963445342
Mean Squared Error: 931476.9037324339
Root Mean Squared Error: 965.1305112431344
R square value is: 0.8348460837179419


In [60]:
print('The accuracy for impressions is:',round(r2_score(y_val, y_pred_linear_val)*100,2),"%")

The accuracy for impressions is: 83.48 %


# Random Forest Regression For Impressions

In [61]:
#fitting Random Forest Regression to the Training set for IMPRESSIONS

regressor_rf = RandomForestRegressor(n_estimators = 50, random_state = 0)
regressor_rf.fit(X_train, y_train)

# Predicting the Test set results
y_pred_rf = regressor_rf.predict(X_test)

In [62]:
# Evaluating the Algorithm for test data for IMPRESSIONS

print('Mean Absolute Error:', metrics.mean_absolute_error(y_test, y_pred_rf))  
print('Mean Squared Error:', metrics.mean_squared_error(y_test, y_pred_rf))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_test, y_pred_rf)))
print('R square value is:',r2_score(y_test, y_pred_rf))

Mean Absolute Error: 134.4133400147079
Mean Squared Error: 3658965.2758217035
Root Mean Squared Error: 1912.8421983586893
R square value is: 0.8290463989368565


In [63]:
#VALIDATION accuracy for RF for IMPRESSIONS

y_pred_rf_val = regressor_rf.predict(X_val)
print('Mean Absolute Error:', metrics.mean_absolute_error(y_val, y_pred_rf_val))  
print('Mean Squared Error:', metrics.mean_squared_error(y_val, y_pred_rf_val))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_val, y_pred_rf_val)))
print('R square value is:',r2_score(y_val, y_pred_rf_val))

Mean Absolute Error: 89.38301201932309
Mean Squared Error: 1256582.1829512743
Root Mean Squared Error: 1120.9737655053639
R square value is: 0.7772038492708851


In [64]:
print('Accuracy with Random Forest method is :',round(r2_score(y_val, y_pred_rf_val)*100,2),"%")

Accuracy with Random Forest method is : 77.72 %


# XGBoost Regression for Impressions

In [65]:
#fitting XGBoost Regression to the Training set for IMPRESSIONS

best_xgb_model = xgboost.XGBRegressor(colsample_bytree=0.4,
                 gamma=0,                 
                 learning_rate=0.07,
                 max_depth=3,
                 min_child_weight=1.5,
                 n_estimators=10000,                                                                    
                 reg_alpha=0.75,
                 reg_lambda=0.45,
                 subsample=0.6,
                 seed=42)
best_xgb_model.fit(X_train, y_train)

# Predicting the Test set results
y_pred_xgboost = best_xgb_model.predict(X_test)

In [66]:
# Evaluating the Algorithm on test data for IMPRESSIONS

print('Mean Absolute Error:', metrics.mean_absolute_error(y_test, y_pred_xgboost))  
print('Mean Squared Error:', metrics.mean_squared_error(y_test, y_pred_xgboost))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_test, y_pred_xgboost)))
print('R square value is:',r2_score(y_test, y_pred_xgboost))

Mean Absolute Error: 139.21769720566593
Mean Squared Error: 2647609.8209844185
Root Mean Squared Error: 1627.147756346798
R square value is: 0.8762987896883538


In [67]:
#validation accuracy for XG boost for IMPRESSIONS
y_pred_xgboost_val = best_xgb_model.predict(X_val)
print('Mean Absolute Error:', metrics.mean_absolute_error(y_val, y_pred_xgboost_val))  
print('Mean Squared Error:', metrics.mean_squared_error(y_val, y_pred_xgboost_val))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_val, y_pred_xgboost_val)))
print('R square value is:',r2_score(y_val, y_pred_xgboost_val))

Mean Absolute Error: 101.55412096238923
Mean Squared Error: 1350078.3574219064
Root Mean Squared Error: 1161.9287230385116
R square value is: 0.7606266702669375


In [68]:
print('XGBoost accuracy for impressions is:',round(r2_score(y_val, y_pred_xgboost_val)*100,2),"%")

XGBoost accuracy for impressions is: 76.06 %


# CLICKS

In [69]:
#Modelling for CLICKS

split_size=0.3

#Creation of Train and Test dataset
X_train, X_test, y_train, y_test = sklearn.model_selection.train_test_split(X,y2,test_size=split_size,random_state=22)

#Creation of Train and validation dataset
X_train, X_val, y_train, y_val = train_test_split(X_train,y_train,test_size=0.2,random_state=5)

# Linear Regression for Clicks 

In [71]:
#Build base linear model as the task is to make predictions with continuos dependent variables.
#fitting Linear Regression to the Training set for CLICKS

regressor_c = LinearRegression()
regressor_c.fit(X_train, y_train)

y_pred_linear_c = regressor_c.predict(X_test)

In [72]:
#Evaluation model for test data for CLICKS

print('Mean Absolute Error:', metrics.mean_absolute_error(y_test, y_pred_linear_c))  
print('Mean Squared Error:', metrics.mean_squared_error(y_test, y_pred_linear_c))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_test, y_pred_linear_c)))
print('R square value is:',r2_score(y_test, y_pred_linear_c))

Mean Absolute Error: 0.5051105167587446
Mean Squared Error: 29.887485610532412
Root Mean Squared Error: 5.466944815025337
R square value is: 0.5627348034557889


In [73]:
#VALIDATION accuracy for LR for CLICKS

y_pred_linear_c_val = regressor_c.predict(X_val)
print('Mean Absolute Error:', metrics.mean_absolute_error(y_val, y_pred_linear_c_val))  
print('Mean Squared Error:', metrics.mean_squared_error(y_val, y_pred_linear_c_val))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_val, y_pred_linear_c_val)))
print('R square value is:',r2_score(y_val, y_pred_linear_c_val))

Mean Absolute Error: 0.3443013485298719
Mean Squared Error: 2.965748594961469
Root Mean Squared Error: 1.7221348945310495
R square value is: 0.6757151658610616


In [74]:
print('Linear Regression accuracy for clicks is:',round(r2_score(y_val, y_pred_linear_c_val)*100,2),"%")

Linear Regression accuracy for clicks is: 67.57 %


# Random Forest Regression for clicks

In [76]:
#fitting Random Forest Regression to the Training set for CLICKS

regressor_rf_c = RandomForestRegressor(n_estimators = 50, random_state = 0)
regressor_rf_c.fit(X_train, y_train)

# Predicting the Test set results
y_pred_rf_c = regressor_rf_c.predict(X_test)

In [77]:
# Evaluating the Algorithm for CLICKS

print('Mean Absolute Error:', metrics.mean_absolute_error(y_test, y_pred_rf_c))  
print('Mean Squared Error:', metrics.mean_squared_error(y_test, y_pred_rf_c))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_test, y_pred_rf_c)))
print('R square value is:',r2_score(y_test, y_pred_rf_c))

Mean Absolute Error: 0.17510238454037763
Mean Squared Error: 13.800321620423722
Root Mean Squared Error: 3.7148784126029915
R square value is: 0.7980960852858974


In [78]:
#VALIDATION accuracy for LR for CLICKS

y_pred_rf_c_val = regressor_rf_c.predict(X_val)
print('Mean Absolute Error:', metrics.mean_absolute_error(y_val, y_pred_rf_c_val))  
print('Mean Squared Error:', metrics.mean_squared_error(y_val, y_pred_rf_c_val))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_val, y_pred_rf_c_val)))
print('R square value is:',r2_score(y_val, y_pred_rf_c_val))

Mean Absolute Error: 0.08767974166587518
Mean Squared Error: 2.0599536138284735
Root Mean Squared Error: 1.4352538499612093
R square value is: 0.7747578074793113


In [79]:
print('Random Forest accuracy for clicks is:',round(r2_score(y_val, y_pred_rf_c_val)*100,2),"%")

Random Forest accuracy for clicks is: 77.48 %


# XGBoost Regression for clicks

In [80]:
#fitting XGBoost Regression to the Training set for CLICKS

best_xgb_model_c = xgboost.XGBRegressor(colsample_bytree=0.4,
                 gamma=0,                 
                 learning_rate=0.07,
                 max_depth=3,
                 min_child_weight=1.5,
                 n_estimators=10000,                                                                    
                 reg_alpha=0.75,
                 reg_lambda=0.45,
                 subsample=0.6,
                 seed=42)
best_xgb_model_c.fit(X_train, y_train)

# Predicting the Test set results
y_pred_xgboost_c = best_xgb_model_c.predict(X_test)

In [81]:
# Evaluating the Algorithm for CLICKS

print('Mean Absolute Error:', metrics.mean_absolute_error(y_test, y_pred_xgboost_c))  
print('Mean Squared Error:', metrics.mean_squared_error(y_test, y_pred_xgboost_c))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_test, y_pred_xgboost_c)))
print('R square value is:',r2_score(y_test, y_pred_xgboost_c))

Mean Absolute Error: 0.22498284963263301
Mean Squared Error: 16.1319414699245
Root Mean Squared Error: 4.016458822137294
R square value is: 0.7639836067373822


In [82]:
#validation accuracy for XG boost for CLICKS
y_pred_xgboost_c_val = best_xgb_model_c.predict(X_val)
print('Mean Absolute Error:', metrics.mean_absolute_error(y_val, y_pred_xgboost_c_val))  
print('Mean Squared Error:', metrics.mean_squared_error(y_val, y_pred_xgboost_c_val))  
print('Root Mean Squared Error:', np.sqrt(metrics.mean_squared_error(y_val, y_pred_xgboost_c_val)))
print('R square value is:',r2_score(y_val, y_pred_xgboost_c_val))

Mean Absolute Error: 0.12277426657324458
Mean Squared Error: 2.4259315674058257
Root Mean Squared Error: 1.557540229787284
R square value is: 0.7347405584866058


In [83]:
print('XGBoost accuracy for clicks is:',round(r2_score(y_val, y_pred_xgboost_c_val)*100,2),"%")

XGBoost accuracy for clicks is: 73.47 %


# Prediction for the Next week

In [84]:
#creating a NEW df to predict the next week value
df_nextweek = pd.DataFrame([{'business_vertical':0, 'country':0, 'channel_name':0, 'goal_type':0,
       'total_spend_cpm': 100, 'ctr':0.2, 'week':41, 'day':4 }])
df_nextweek.head()

business_vertical  country  channel_name  goal_type  total_spend_cpm  ctr  \
0                  0        0             0          0              100  0.2   

   week  day  
0    41    4

In [85]:
#choosing the best model for IMPRESIONS ie XGBoost to predict value
y_pred_nextweek = best_xgb_model.predict(df_nextweek)

In [86]:
y_pred_nextweek

array([-331.41333], dtype=float32)

In [90]:
print("The Impressions for the next week is going to be:",abs(y_pred_nextweek[0]))

The Impressions for the next week is going to be: 331.41333


In [91]:
#choosing the best model for CLICKS ie RF model to predict value
y_pred_nextweek_c = regressor_rf_c.predict(df_nextweek)

In [93]:
y_pred_nextweek_c

array([1.])

In [94]:
print("The clicks for the week is going to be:",y_pred_nextweek_c[0])

The clicks for the week is going to be: 1.0


In [97]:
import pandas as pd

#create data
df = pd.DataFrame({'Target variables': ["Impressions","Clicks"],
                   'Linear Regression': ["83.48%","67.57%"],
                   'Random Forest Regression': ["77.72%","77.48%"],
                  'XGBoost Regression': ["76.06%","73.47%"] })


In [98]:
df

Target variables Linear Regression Random Forest Regression  \
0      Impressions            83.48%                   77.72%   
1           Clicks            67.57%                   77.48%   

  XGBoost Regression  
0             76.06%  
1             73.47%